## 04. Interactive Maps 

In [46]:
import folium 
import geopandas as gpd 
import os 
import pandas as pd
import pathlib 

from folium.plugins import HeatMap, HeatMapWithTime

os.chdir('..')
path = pathlib.Path().resolve() 

#### 1. Read data

In [2]:
countries = gpd.read_file(gpd.datasets.get_path('naturalearth_lowres')) 
acled = gpd.read_file(f'{path}/data/acled2019.shp', mask = countries[countries['continent'] == 'Africa']) 

In [3]:
acled.head()

data_id  iso event_id_c  event_id_n        event_date  year  time_preci  \
0  6768128  887   YEM45982       45982  31 December 2019  2019           1   
1  6768129  887   YEM45983       45983  31 December 2019  2019           1   
2  6768130  887   YEM45984       45984  31 December 2019  2019           1   
3  6714129  706   SOM30213       30213  31 December 2019  2019           1   
4  6760978  887   YEM45977       45977  31 December 2019  2019           1   

               event_type                sub_event_  \
0                 Battles               Armed clash   
1  Strategic developments  Change to group/activity   
2                 Battles               Armed clash   
3                 Battles               Armed clash   
4  Strategic developments  Change to group/activity   

                                              actor1  ... latitude  longitude  \
0                   Military Forces of Yemen (2012-)  ...  14.3541    47.0765   
1  Military Forces of Yemen (2012-) Security Belt...  ...  14.3541    47.0765   
2                   Military Forces of Yemen (2012-)  ...  14.2081    47.1570   
3                                         Al Shabaab  ...   2.3963    45.0159   
4                           Operation Restoring Hope  ...  14.9403    46.6711   

  geo_precis                                             source  \
0          2  Yemen Data Project; Aden al Ghad; Al Janoob al...   
1          2              Al Janoob al Youm; Yemen Data Project   
2          1  Al Janoob al Youm; Aden al Ghad; Yemen Data Pr...   
3          1                                 Undisclosed Source   
4          1                 YNP; Yemen Data Project; Al Masdar   

               source_sca                                              notes  \
0  Local partner-National  On 31 December 2019, clashes reportedly erupte...   
1  Local partner-National  On 31 December 2019, forces loyal to the South...   
2  Local partner-National  On 31 December 2019, clashes reportedly erupte...   
3     Local partner-Other  31 December 2019. In Warmahan, Al Shabaab mili...   
4  Local partner-National  On 31 December 2019, Sudanese forces reportedl...   

  fatalities   timestamp iso3                   geometry  
0          0  1580761030  YEM  POINT (47.07650 14.35410)  
1          0  1580761030  YEM  POINT (47.07650 14.35410)  
2          1  1580761030  YEM  POINT (47.15700 14.20810)  
3          0  1578512393  SOM   POINT (45.01590 2.39630)  
4          0  1580153672  YEM  POINT (46.67110 14.94030)  

[5 rows x 32 columns]

#### 2. Base maps

In [4]:
m = folium.Map(location=[47.07650, 14.35410], zoom_start = 20)
m

We can use other base maps 

In [5]:
location=[47.07650, 14.35410]
m = folium.Map(location=location, tiles="CartoDB dark_matter", zoom_start = 20)
m

Mark things on the map: 

In [6]:
folium.Marker(location=location, popup='<i> Pinned Place </i>').add_to(m)
m

Adding a circle marker: 

In [7]:
folium.Circle(location = location, radius = 25, popup='Marked Circle', color = 'red', fill = False).add_to(m)
m

In [8]:
m = folium.Map(location, zoom_start=2, tiles='cartodbpositron')

folium.GeoJson(acled.sample(1000)).add_to(m)
m

Changing marker in `Folium`: 

In [9]:
m = folium.Map(location, zoom_start=2, tiles='cartodbpositron')
acled_sample = acled.sample(1000)
locs_points = zip(acled_sample.geometry.y, acled_sample.geometry.x) 

for location in locs_points:
    folium.CircleMarker(location=location, color='red', radius=0.5).add_to(m)
m

Marker cluster
- useful when maps need to shrink and expend often 

In [10]:
from folium.plugins import FastMarkerCluster

cmap = folium.Map(location=location, zoom_start=2, tiles='cartodbpositron')

FastMarkerCluster(data=list(zip(acled_sample.geometry.y.values, acled_sample.geometry.x.values))).add_to(cmap)
cmap

### 3. Heatmaps

In [16]:
df = acled[['latitude', 'longitude']]
df.head()

latitude  longitude
0   14.3541    47.0765
1   14.3541    47.0765
2   14.2081    47.1570
3    2.3963    45.0159
4   14.9403    46.6711

In [17]:
heat_data = list(df.values)
heat_data[:10]

[array([14.3541, 47.0765]),
 array([14.3541, 47.0765]),
 array([14.2081, 47.157 ]),
 array([ 2.3963, 45.0159]),
 array([14.9403, 46.6711]),
 array([31.0167, 47.4333]),
 array([13.9667, 48.1833]),
 array([36.7525,  3.042 ]),
 array([36.365 ,  6.6147]),
 array([-3.3543, 40.0209])]

In [27]:
maps = folium.Map(location=[14.3541, 47.0765], tiles='cartodbpositron', zoom_start = 4)
HeatMap(heat_data).add_to(maps)
maps

We can change colors of the heatmap: 

In [36]:
gradient = {'0.0':'blue', '1.0' :'red'}

In [37]:
location = [14.3541, 47.0765]
maps = folium.Map(location=location, zoom_start=5, tiles='OpenStreetMap')

HeatMap(heat_data, gradient=gradient).add_to(maps)
maps

### 4. Animated Heatmaps: 

For animation we need to add column with time 

In [62]:
heatmap_time = acled[['latitude', 'longitude', 'event_date']]
heatmap_time.event_date = pd.to_datetime(heatmap_time.event_date)
len(heatmap_time.event_date.unique())

/var/folders/2f/c6skwjt96m984f45rzp9_qw40000gn/T/ipykernel_51016/101287512.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  heatmap_time.event_date = pd.to_datetime(heatmap_time.event_date)


365

In [68]:
heatmap_time.event_date.min()

Timestamp('2019-01-01 00:00:00')

In [71]:
heatmap_time.event_date.max()

Timestamp('2019-12-31 00:00:00')

In [73]:
from dateutil.rrule import rrule, DAILY
heatmap_time_data = [[[row['latitude'], row['longitude']] for index, row in heatmap_time[heatmap_time['event_date'] == i].iterrows()] for i in rrule(
    DAILY,
    dtstart=heatmap_time.event_date.min(),
    until=heatmap_time.event_date.max())]
    

In [75]:
heatmap_time_data[1]

[[35.7233, 36.7135],
 [35.4191, 36.4384],
 [35.8398, 36.6415],
 [9.5091, -13.7122],
 [31.2089, 16.5887],
 [35.1939, -0.6414],
 [35.7083, 36.805],
 [22.785, 5.5228],
 [13.6957, 44.7314],
 [2.8142, 46.1252],
 [-10.7822, 40.4811],
 [-3.0804, 29.391],
 [35.317, 36.6676],
 [-2.8373, 30.2941],
 [-2.8114, 29.9495],
 [10.9901, 49.0568],
 [33.5928, -7.6192],
 [31.3059, 45.2799],
 [2.0333, 45.35],
 [2.0195, 45.31],
 [2.0678, 45.35],
 [2.0652, 45.39],
 [5.4521, 10.1932],
 [31.769000000000002, 35.2163],
 [32.766999999999996, 22.6367],
 [35.3213, 36.6204],
 [15.5725, 32.5364],
 [35.3406, 36.5777],
 [4.3704, 18.5395],
 [35.3533, 36.5582],
 [35.3469, 36.5366],
 [35.3739, 36.6893],
 [35.4144, 36.5098],
 [12.7833, 7.0],
 [35.6848, 36.3387],
 [14.1836, 43.2264],
 [30.436999999999998, 49.1029],
 [35.3319, 40.1461],
 [-17.3269, 35.5842],
 [31.7878, 35.2211],
 [35.5475, 36.644],
 [37.1683, 43.2709],
 [35.4781, 36.836],
 [9.033, 38.7],
 [35.6162, 36.2693],
 [12.1628, 6.6614],
 [36.285, 36.8511],
 [26.2175, 

In [77]:
maps = folium.Map(location=location, zoom_start=4, tiles='OpenStreetMap')

HeatMapWithTime(heatmap_time_data, auto_play = True).add_to(maps)
maps